In [1]:
import sys

sys.path.append('/user/ms5941/NLP')

from config import *
from utilities import *

import gensim

import glob
import os
import re

import numpy as np
import pandas as pd

import json



import logging
logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.INFO)

from gensim.models import ldaseqmodel



/user/ms5941/.local/lib/python3.7/site-packages/gensim/similarities/__init__.py:15: UserWarning: The gensim.similarities.levenshtein submodule is disabled, because the optional Levenshtein package <https://pypi.org/project/python-Levenshtein/> is unavailable. Install Levenhstein (e.g. `pip install python-Levenshtein`) to suppress this warning.
  warnings.warn(msg)


In [ ]:
THEME = 'Volatility'

Trying the seq model for 3 months on the original dictionary.

In [4]:
time_slices = pd.read_csv('Summary Stat Tables/%s_Article_Count.csv' % THEME, index_col=0)
time_slices.sort_index(inplace=True)
time_slices.index = pd.to_datetime(time_slices.index)
time_slices.groupby(time_slices.index.year)['No. of Volatility Articles'].sum()

1996    12537
1997    17826
1998    38090
1999    23782
2000    20482
2001    17410
2002    38270
2003    35783
2004    53714
2005    60909
2006    71759
2007    45081
2008    31186
2009    26690
2010    36037
2011    49749
2012    36236
2013    55035
2014    82909
2015    66845
2016    42241
2017    45781
2018    90243
2019    81747
2020    79733
Name: No. of Volatility Articles, dtype: int64

In [9]:
slices_1996 = time_slices.sort_index()[:12]['No. of Volatility Articles'].values

In [17]:
ldaseq = ldaseqmodel.LdaSeqModel(corpus=corpus_all[:3180], 
                                 id2word=dictionary_all, 
                                 time_slice=slices_1996[:3], 
                                 num_topics=5,
                                 em_min_iter=1,
                                 em_max_iter=1,
                                 chunksize=2000)

2021-04-25 17:01:46,823 : INFO : using symmetric eta at 0.2
2021-04-25 17:01:46,868 : INFO : using serial LDA version on this node
2021-04-25 17:01:47,053 : INFO : running online (multi-pass) LDA training, 5 topics, 10 passes over the supplied corpus of 3180 documents, updating model once every 2000 documents, evaluating perplexity every 3180 documents, iterating 50x with a convergence threshold of 0.001000
2021-04-25 17:01:48,075 : INFO : PROGRESS: pass 0, at document #2000/3180
2021-04-25 17:01:49,489 : INFO : merging changes from 2000 documents into a model of 3180 documents
2021-04-25 17:01:49,569 : INFO : topic #0 (0.010): 0.002*"jan" + 0.002*"billion" + 0.002*"inc" + 0.002*"next" + 0.002*"feb" + 0.001*"japan" + 0.001*"added" + 0.001*"japanese" + 0.001*"investors" + 0.001*"rally"
2021-04-25 17:01:49,573 : INFO : topic #1 (0.010): 0.002*"month" + 0.002*"cattle" + 0.002*"march" + 0.002*"term" + 0.002*"jan" + 0.002*"feb" + 0.002*"see" + 0.002*"europe" + 0.002*"bank" + 0.002*"trader"


In [18]:
ldaseq.print_topics(time=0)

[[('gold', 0.036321370172212104),
  ('peru', 0.020222271494958866),
  ('mining', 0.019435406754405256),
  ('output', 0.015071967932882603),
  ('mou', 0.014580408082888652),
  ('exploration', 0.012379061778917448),
  ('mines', 0.011224283287531216),
  ('media', 0.010144758595017709),
  ('yanacocha', 0.009790077591913617),
  ('ounces', 0.009446782203788234),
  ('cheese', 0.009265523360245574),
  ('chapter', 0.008736019791843798),
  ('law', 0.007727356978228695),
  ('officials', 0.0077102582364995545),
  ('miners', 0.0075288580402089215),
  ('society', 0.007472512180435983),
  ('rights', 0.007466324517776847),
  ('slovakia', 0.006612233817653739),
  ('human', 0.006367044404625608),
  ('fruit', 0.006207997530268435)],
 [('cattle', 0.03335820332793832),
  ('hog', 0.018570301444040118),
  ('live', 0.015480697592451778),
  ('buchanan', 0.012780782876958949),
  ('beef', 0.012361147367594914),
  ('feeder', 0.009969817763484393),
  ('clinton', 0.009816118770227351),
  ('republican', 0.0097618389

Looking at the above words, clean up the dictionari

In [60]:
# Checking each dictionary

In [90]:
filter_dictionary('Inflation')

2021-04-25 19:50:14,481 : INFO : loading Dictionary object from /work/ms5941/NLP/Temp/Inflation/Inflation.dict
2021-04-25 19:50:14,795 : INFO : Dictionary lifecycle event {'fname': '/work/ms5941/NLP/Temp/Inflation/Inflation.dict', 'datetime': '2021-04-25T19:50:14.795559', 'gensim': '4.0.1', 'python': '3.7.7 (default, May  7 2020, 21:25:33) \n[GCC 7.3.0]', 'platform': 'Linux-4.19.0-16-amd64-x86_64-with-debian-10.9', 'event': 'loaded'}


Length of old dictionary: 454809


2021-04-25 19:50:40,950 : INFO : discarding 453922 tokens: [('abducted', 2611), ('alex', 16963), ('attacks', 75162), ('attempt', 36261), ('boncayao', 4), ('boy', 7460), ('brigade', 1309), ('businessmen', 3821), ('chamber', 16444), ('claimed', 12646)]...
2021-04-25 19:50:40,951 : INFO : keeping 887 tokens which were in no less than 100000 and no more than 1815322 (=80.0%) documents
2021-04-25 19:50:41,107 : INFO : resulting dictionary: Dictionary(887 unique tokens: ['action', 'american', 'board', 'chinese', 'come']...)
2021-04-25 19:50:41,144 : INFO : Dictionary lifecycle event {'fname_or_handle': '/work/ms5941/NLP/Temp/Inflation/Inflation_clean.dict', 'separately': 'None', 'sep_limit': 10485760, 'ignore': frozenset(), 'datetime': '2021-04-25T19:50:41.144927', 'gensim': '4.0.1', 'python': '3.7.7 (default, May  7 2020, 21:25:33) \n[GCC 7.3.0]', 'platform': 'Linux-4.19.0-16-amd64-x86_64-with-debian-10.9', 'event': 'saving'}
2021-04-25 19:50:41,161 : INFO : saved /work/ms5941/NLP/Temp/Infl

Clean dictionary saved! New Length:  828


In [91]:
filter_dictionary('GDP')

2021-04-25 19:50:51,639 : INFO : loading Dictionary object from /work/ms5941/NLP/Temp/GDP/GDP.dict
2021-04-25 19:50:51,941 : INFO : Dictionary lifecycle event {'fname': '/work/ms5941/NLP/Temp/GDP/GDP.dict', 'datetime': '2021-04-25T19:50:51.941477', 'gensim': '4.0.1', 'python': '3.7.7 (default, May  7 2020, 21:25:33) \n[GCC 7.3.0]', 'platform': 'Linux-4.19.0-16-amd64-x86_64-with-debian-10.9', 'event': 'loaded'}


Length of old dictionary: 447423


2021-04-25 19:50:53,112 : INFO : discarding 446527 tokens: [('abducted', 3449), ('alex', 17980), ('attacks', 79356), ('attempt', 36852), ('boncayao', 4), ('boy', 8562), ('brigade', 1139), ('businessmen', 3903), ('chamber', 16157), ('claimed', 12935)]...
2021-04-25 19:50:53,127 : INFO : keeping 896 tokens which were in no less than 100000 and no more than 1932826 (=80.0%) documents
2021-04-25 19:50:53,257 : INFO : resulting dictionary: Dictionary(896 unique tokens: ['action', 'american', 'board', 'chinese', 'come']...)
2021-04-25 19:50:53,307 : INFO : Dictionary lifecycle event {'fname_or_handle': '/work/ms5941/NLP/Temp/GDP/GDP_clean.dict', 'separately': 'None', 'sep_limit': 10485760, 'ignore': frozenset(), 'datetime': '2021-04-25T19:50:53.307727', 'gensim': '4.0.1', 'python': '3.7.7 (default, May  7 2020, 21:25:33) \n[GCC 7.3.0]', 'platform': 'Linux-4.19.0-16-amd64-x86_64-with-debian-10.9', 'event': 'saving'}
2021-04-25 19:50:53,312 : INFO : saved /work/ms5941/NLP/Temp/GDP/GDP_clean.di

Clean dictionary saved! New Length:  837


In [92]:
filter_dictionary('Volatility')

2021-04-25 19:51:04,174 : INFO : loading Dictionary object from /work/ms5941/NLP/Temp/Volatility/Volatility.dict
2021-04-25 19:51:04,401 : INFO : Dictionary lifecycle event {'fname': '/work/ms5941/NLP/Temp/Volatility/Volatility.dict', 'datetime': '2021-04-25T19:51:04.401485', 'gensim': '4.0.1', 'python': '3.7.7 (default, May  7 2020, 21:25:33) \n[GCC 7.3.0]', 'platform': 'Linux-4.19.0-16-amd64-x86_64-with-debian-10.9', 'event': 'loaded'}


Length of old dictionary: 338298


2021-04-25 19:51:05,200 : INFO : discarding 337766 tokens: [('adjusted', 51333), ('adjustment', 17222), ('announcing', 7365), ('approved', 34917), ('asked', 44421), ('base', 96045), ('beef', 18144), ('buffer', 4027), ('caltex', 551), ('centavo', 44)]...
2021-04-25 19:51:05,214 : INFO : keeping 532 tokens which were in no less than 100000 and no more than 928060 (=80.0%) documents
2021-04-25 19:51:05,309 : INFO : resulting dictionary: Dictionary(532 unique tokens: ['added', 'additional', 'agency', 'average', 'based']...)
2021-04-25 19:51:05,330 : INFO : Dictionary lifecycle event {'fname_or_handle': '/work/ms5941/NLP/Temp/Volatility/Volatility_clean.dict', 'separately': 'None', 'sep_limit': 10485760, 'ignore': frozenset(), 'datetime': '2021-04-25T19:51:05.330686', 'gensim': '4.0.1', 'python': '3.7.7 (default, May  7 2020, 21:25:33) \n[GCC 7.3.0]', 'platform': 'Linux-4.19.0-16-amd64-x86_64-with-debian-10.9', 'event': 'saving'}
2021-04-25 19:51:05,357 : INFO : saved /work/ms5941/NLP/Temp/

Clean dictionary saved! New Length:  480


In [94]:
create_new_corpuses('Volatility')

['1996', '1997', '1998', '1999', '2000', '2001', '2002', '2003', '2004', '2005', '2006', '2007', '2008', '2009', '2010', '2011', '2012', '2013', '2014', '2015', '2016', '2017', '2018', '2019', '2020']
/work/ms5941/NLP/Temp/Volatility/Volatility_Articles_Tokenized_1996.json done!
/work/ms5941/NLP/Temp/Volatility/Volatility_Articles_Tokenized_1997.json done!
/work/ms5941/NLP/Temp/Volatility/Volatility_Articles_Tokenized_1998.json done!
/work/ms5941/NLP/Temp/Volatility/Volatility_Articles_Tokenized_1999.json done!
/work/ms5941/NLP/Temp/Volatility/Volatility_Articles_Tokenized_2000.json done!
/work/ms5941/NLP/Temp/Volatility/Volatility_Articles_Tokenized_2001.json done!
/work/ms5941/NLP/Temp/Volatility/Volatility_Articles_Tokenized_2002.json done!
/work/ms5941/NLP/Temp/Volatility/Volatility_Articles_Tokenized_2003.json done!
/work/ms5941/NLP/Temp/Volatility/Volatility_Articles_Tokenized_2004.json done!
/work/ms5941/NLP/Temp/Volatility/Volatility_Articles_Tokenized_2005.json done!
/work/ms5

2021-04-25 19:52:39,241 : INFO : loading Dictionary object from /work/ms5941/NLP/Temp/Volatility/Volatility_clean.dict
2021-04-25 19:52:39,244 : INFO : Dictionary lifecycle event {'fname': '/work/ms5941/NLP/Temp/Volatility/Volatility_clean.dict', 'datetime': '2021-04-25T19:52:39.244144', 'gensim': '4.0.1', 'python': '3.7.7 (default, May  7 2020, 21:25:33) \n[GCC 7.3.0]', 'platform': 'Linux-4.19.0-16-amd64-x86_64-with-debian-10.9', 'event': 'loaded'}
2021-04-25 19:52:39,245 : INFO : storing corpus in Matrix Market format to /work/ms5941/NLP/Temp/Volatility/Volatility_clean.mm
2021-04-25 19:52:39,311 : INFO : saving sparse matrix to /work/ms5941/NLP/Temp/Volatility/Volatility_clean.mm
2021-04-25 19:52:39,312 : INFO : PROGRESS: saving document #0
2021-04-25 19:52:39,399 : INFO : PROGRESS: saving document #1000


/work/ms5941/NLP/Temp/Volatility/Volatility_Articles_Tokenized_2020.json done!
<__main__.create_new_corpuses.<locals>.MyCorpus object at 0x1463e7497650>


2021-04-25 19:52:39,490 : INFO : PROGRESS: saving document #2000
2021-04-25 19:52:39,578 : INFO : PROGRESS: saving document #3000
2021-04-25 19:52:39,667 : INFO : PROGRESS: saving document #4000
2021-04-25 19:52:39,760 : INFO : PROGRESS: saving document #5000
2021-04-25 19:52:39,853 : INFO : PROGRESS: saving document #6000
2021-04-25 19:52:39,948 : INFO : PROGRESS: saving document #7000
2021-04-25 19:52:40,052 : INFO : PROGRESS: saving document #8000
2021-04-25 19:52:40,150 : INFO : PROGRESS: saving document #9000
2021-04-25 19:52:40,261 : INFO : PROGRESS: saving document #10000
2021-04-25 19:52:40,401 : INFO : PROGRESS: saving document #11000
2021-04-25 19:52:40,497 : INFO : PROGRESS: saving document #12000
2021-04-25 19:52:40,601 : INFO : PROGRESS: saving document #13000
2021-04-25 19:52:40,705 : INFO : PROGRESS: saving document #14000
2021-04-25 19:52:40,805 : INFO : PROGRESS: saving document #15000
2021-04-25 19:52:40,915 : INFO : PROGRESS: saving document #16000
2021-04-25 19:52:4

In [95]:
create_new_corpuses('Inflation', end_year=2018)

['1996', '1997', '1998', '1999', '2000', '2001', '2002', '2003', '2004', '2005', '2006', '2007', '2008', '2009', '2010', '2011', '2012', '2013', '2014', '2015', '2016', '2017', '2018']
/work/ms5941/NLP/Temp/Inflation/Inflation_Articles_Tokenized_1996.json done!
/work/ms5941/NLP/Temp/Inflation/Inflation_Articles_Tokenized_1997.json done!
/work/ms5941/NLP/Temp/Inflation/Inflation_Articles_Tokenized_1998.json done!
/work/ms5941/NLP/Temp/Inflation/Inflation_Articles_Tokenized_1999.json done!
/work/ms5941/NLP/Temp/Inflation/Inflation_Articles_Tokenized_2000.json done!
/work/ms5941/NLP/Temp/Inflation/Inflation_Articles_Tokenized_2001.json done!
/work/ms5941/NLP/Temp/Inflation/Inflation_Articles_Tokenized_2002.json done!
/work/ms5941/NLP/Temp/Inflation/Inflation_Articles_Tokenized_2003.json done!
/work/ms5941/NLP/Temp/Inflation/Inflation_Articles_Tokenized_2004.json done!
/work/ms5941/NLP/Temp/Inflation/Inflation_Articles_Tokenized_2005.json done!
/work/ms5941/NLP/Temp/Inflation/Inflation_Art

2021-04-25 19:57:50,477 : INFO : loading Dictionary object from /work/ms5941/NLP/Temp/Inflation/Inflation_clean.dict
2021-04-25 19:57:50,479 : INFO : Dictionary lifecycle event {'fname': '/work/ms5941/NLP/Temp/Inflation/Inflation_clean.dict', 'datetime': '2021-04-25T19:57:50.479724', 'gensim': '4.0.1', 'python': '3.7.7 (default, May  7 2020, 21:25:33) \n[GCC 7.3.0]', 'platform': 'Linux-4.19.0-16-amd64-x86_64-with-debian-10.9', 'event': 'loaded'}
2021-04-25 19:57:50,480 : INFO : storing corpus in Matrix Market format to /work/ms5941/NLP/Temp/Inflation/Inflation_clean.mm
2021-04-25 19:57:50,660 : INFO : saving sparse matrix to /work/ms5941/NLP/Temp/Inflation/Inflation_clean.mm
2021-04-25 19:57:50,662 : INFO : PROGRESS: saving document #0


/work/ms5941/NLP/Temp/Inflation/Inflation_Articles_Tokenized_2018.json done!
<__main__.create_new_corpuses.<locals>.MyCorpus object at 0x1465cb037490>


2021-04-25 19:57:50,775 : INFO : PROGRESS: saving document #1000
2021-04-25 19:57:50,880 : INFO : PROGRESS: saving document #2000
2021-04-25 19:57:50,988 : INFO : PROGRESS: saving document #3000
2021-04-25 19:57:51,100 : INFO : PROGRESS: saving document #4000
2021-04-25 19:57:51,211 : INFO : PROGRESS: saving document #5000
2021-04-25 19:57:51,324 : INFO : PROGRESS: saving document #6000
2021-04-25 19:57:51,432 : INFO : PROGRESS: saving document #7000
2021-04-25 19:57:51,540 : INFO : PROGRESS: saving document #8000
2021-04-25 19:57:51,656 : INFO : PROGRESS: saving document #9000
2021-04-25 19:57:51,772 : INFO : PROGRESS: saving document #10000
2021-04-25 19:57:51,889 : INFO : PROGRESS: saving document #11000
2021-04-25 19:57:52,002 : INFO : PROGRESS: saving document #12000
2021-04-25 19:57:52,115 : INFO : PROGRESS: saving document #13000
2021-04-25 19:57:52,231 : INFO : PROGRESS: saving document #14000
2021-04-25 19:57:52,351 : INFO : PROGRESS: saving document #15000
2021-04-25 19:57:52

In [96]:
create_new_corpuses('GDP', end_year=2016)

['1996', '1997', '1998', '1999', '2000', '2001', '2002', '2003', '2004', '2005', '2006', '2007', '2008', '2009', '2010', '2011', '2012', '2013', '2014', '2015', '2016']
/work/ms5941/NLP/Temp/GDP/GDP_Articles_Tokenized_1996.json done!
/work/ms5941/NLP/Temp/GDP/GDP_Articles_Tokenized_1997.json done!
/work/ms5941/NLP/Temp/GDP/GDP_Articles_Tokenized_1998.json done!
/work/ms5941/NLP/Temp/GDP/GDP_Articles_Tokenized_1999.json done!
/work/ms5941/NLP/Temp/GDP/GDP_Articles_Tokenized_2000.json done!
/work/ms5941/NLP/Temp/GDP/GDP_Articles_Tokenized_2001.json done!
/work/ms5941/NLP/Temp/GDP/GDP_Articles_Tokenized_2002.json done!
/work/ms5941/NLP/Temp/GDP/GDP_Articles_Tokenized_2003.json done!
/work/ms5941/NLP/Temp/GDP/GDP_Articles_Tokenized_2004.json done!
/work/ms5941/NLP/Temp/GDP/GDP_Articles_Tokenized_2005.json done!
/work/ms5941/NLP/Temp/GDP/GDP_Articles_Tokenized_2006.json done!
/work/ms5941/NLP/Temp/GDP/GDP_Articles_Tokenized_2007.json done!
/work/ms5941/NLP/Temp/GDP/GDP_Articles_Tokenized_20

2021-04-25 20:07:42,822 : INFO : loading Dictionary object from /work/ms5941/NLP/Temp/GDP/GDP_clean.dict
2021-04-25 20:07:42,824 : INFO : Dictionary lifecycle event {'fname': '/work/ms5941/NLP/Temp/GDP/GDP_clean.dict', 'datetime': '2021-04-25T20:07:42.824754', 'gensim': '4.0.1', 'python': '3.7.7 (default, May  7 2020, 21:25:33) \n[GCC 7.3.0]', 'platform': 'Linux-4.19.0-16-amd64-x86_64-with-debian-10.9', 'event': 'loaded'}
2021-04-25 20:07:42,826 : INFO : storing corpus in Matrix Market format to /work/ms5941/NLP/Temp/GDP/GDP_clean.mm
2021-04-25 20:07:43,019 : INFO : saving sparse matrix to /work/ms5941/NLP/Temp/GDP/GDP_clean.mm


/work/ms5941/NLP/Temp/GDP/GDP_Articles_Tokenized_2016.json done!
<__main__.create_new_corpuses.<locals>.MyCorpus object at 0x1461bfb33dd0>


2021-04-25 20:07:43,022 : INFO : PROGRESS: saving document #0
2021-04-25 20:07:43,132 : INFO : PROGRESS: saving document #1000
2021-04-25 20:07:43,239 : INFO : PROGRESS: saving document #2000
2021-04-25 20:07:43,348 : INFO : PROGRESS: saving document #3000
2021-04-25 20:07:43,449 : INFO : PROGRESS: saving document #4000
2021-04-25 20:07:43,555 : INFO : PROGRESS: saving document #5000
2021-04-25 20:07:43,666 : INFO : PROGRESS: saving document #6000
2021-04-25 20:07:43,772 : INFO : PROGRESS: saving document #7000
2021-04-25 20:07:43,873 : INFO : PROGRESS: saving document #8000
2021-04-25 20:07:43,985 : INFO : PROGRESS: saving document #9000
2021-04-25 20:07:44,095 : INFO : PROGRESS: saving document #10000
2021-04-25 20:07:44,204 : INFO : PROGRESS: saving document #11000
2021-04-25 20:07:44,314 : INFO : PROGRESS: saving document #12000
2021-04-25 20:07:44,426 : INFO : PROGRESS: saving document #13000
2021-04-25 20:07:44,534 : INFO : PROGRESS: saving document #14000
2021-04-25 20:07:44,650

In [97]:

THEME = 'GDP'

time_slices = pd.read_csv('Summary Stat Tables/%s_Article_Count.csv' % THEME, index_col=0)
time_slices.sort_index(inplace=True)
time_slices.index = pd.to_datetime(time_slices.index)
# time_slices.groupby(time_slices.index.year)['No. of Volatility Articles'].sum()

yearly_slices = time_slices.groupby(time_slices.index.year)['No. of %s Articles' % THEME].sum().values[:-4]

yearly_slices.sum()

# Load dictionary and corpus
dictionary_all = gensim.corpora.Dictionary.load(TEMP_PATH + '/%s/%s_clean.dict' % (THEME, THEME))
corpus_all = gensim.corpora.MmCorpus(TEMP_PATH + '/%s/%s_clean.mm' % (THEME, THEME))

len(corpus_all)

In [ ]:
ldaseq = ldaseqmodel.LdaSeqModel(corpus=corpus_all, 
                                 id2word=dictionary_all, 
                                 time_slice=yearly_slices, 
                                 passes=2,
                                 num_topics=10,
                                 em_min_iter=1,
                                 em_max_iter=1,
                                 chunksize=12000)

2021-04-25 20:17:29,968 : INFO : using symmetric eta at 0.1
2021-04-25 20:17:29,970 : INFO : using serial LDA version on this node
2021-04-25 20:17:29,972 : INFO : running online (multi-pass) LDA training, 10 topics, 2 passes over the supplied corpus of 2416033 documents, updating model once every 2000 documents, evaluating perplexity every 20000 documents, iterating 50x with a convergence threshold of 0.001000
2021-04-25 20:17:44,117 : INFO : PROGRESS: pass 0, at document #2000/2416033
2021-04-25 20:17:45,339 : INFO : merging changes from 2000 documents into a model of 2416033 documents
2021-04-25 20:17:45,342 : INFO : topic #1 (0.010): 0.013*"mark" + 0.011*"europe" + 0.010*"german" + 0.008*"budget" + 0.007*"high" + 0.007*"report" + 0.007*"three" + 0.007*"france" + 0.006*"germany" + 0.006*"futures"
2021-04-25 20:17:45,343 : INFO : topic #4 (0.010): 0.016*"department" + 0.014*"due" + 0.012*"budget" + 0.009*"president" + 0.009*"china" + 0.008*"report" + 0.007*"high" + 0.007*"labor" + 0.

In [ ]:
ldaseq